# Warum ist es wichtig Elon Musk Tweets zu generieren?
Elon Musk ist seit 2020 der reichste Mann der Welt. Zusätzlich ist er eine der einflussreichsten Personen auf der Plattform und baut diesen Einfluss damit aus, dass der seit 2022 der größte Anteilseigner der Plattform ist. Beim Theman Unternehmensanteile, Elon Musk und Twitter wird es auch abseits von Elon Musks persönlicher Finanzlage interessant. Musk ist bekannt dafür, in den letzten Jahren mit seinen Tweets Aktienkurse beeinflusst zu haben. Er hat beispielsweise 2002....
Wer finanzielle Interessen hat, könnte sich davon ausgehen damit beschäftigen, ein System zu entwickeln, das anhand von Elon Musks Meinung Aktien und Optionen kauft.
Wer finanzielle Interessen hat, sollte sich aber vielleicht auch nicht mit Elon Musks Tweets beschäftigen und denken, dass er anhand dessen der nächste Warren Buffet wird, sondern richtig arbeiten. Viel interessanter wäre es doch eigene Tweets zu generieren.

In [2]:
import numpy as np
import pandas as pd
import tensorflow as tf
from sklearn.model_selection import train_test_split
import os
import torch
import datasets
from transformers import DefaultDataCollator, pipeline, AutoTokenizer, AutoModelForCausalLM, TFGPT2LMHeadModel, AdamWeightDecay, TFAutoModelForCausalLM

2022-06-02 17:50:40.505221: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


## Daten vorbereiten

In [3]:
tweets_from_years = {}

In [4]:
for i in os.listdir('musktweets'):
    year = i.rstrip('.csv')
    print(i)
    if i == '2021.csv' or i == '2022.csv':
        tweets_from_years[year] = pd.read_csv('musktweets/'+i)
    else:
        tweets_from_years[year] = pd.read_csv('musktweets/'+i, index_col='index')

2020.csv
2021.csv
2022.csv
2019.csv
2018.csv
2015.csv
2014.csv
2016.csv
2017.csv
2013.csv
2012.csv
2010.csv
2011.csv


In [5]:
sorted(tweets_from_years['2020'].columns)

['cashtags',
 'conversation_id',
 'created_at',
 'date',
 'day',
 'geo',
 'hashtags',
 'hour',
 'id',
 'language',
 'link',
 'name',
 'near',
 'nlikes',
 'nreplies',
 'nretweets',
 'photos',
 'place',
 'quote_url',
 'reply_to',
 'retweet',
 'retweet_date',
 'retweet_id',
 'search',
 'source',
 'thumbnail',
 'timezone',
 'trans_dest',
 'trans_src',
 'translate',
 'tweet',
 'urls',
 'user_id',
 'user_id_str',
 'user_rt',
 'user_rt_id',
 'username',
 'video']

In [6]:
sorted(tweets_from_years['2022'].columns)

['cashtags',
 'conversation_id',
 'created_at',
 'date',
 'geo',
 'hashtags',
 'id',
 'language',
 'likes_count',
 'link',
 'mentions',
 'name',
 'near',
 'photos',
 'place',
 'quote_url',
 'replies_count',
 'reply_to',
 'retweet',
 'retweet_date',
 'retweet_id',
 'retweets_count',
 'source',
 'thumbnail',
 'time',
 'timezone',
 'trans_dest',
 'trans_src',
 'translate',
 'tweet',
 'urls',
 'user_id',
 'user_rt',
 'user_rt_id',
 'username',
 'video']

In [7]:
for year in tweets_from_years:
    if year == '2022' or year == '2021' or year == '2020':
        tweets_from_years[year].rename(columns={'likes_count':'nlikes'}, inplace=True)
        print(tweets_from_years[year].columns)

Index(['id', 'conversation_id', 'created_at', 'date', 'timezone', 'place',
       'tweet', 'language', 'hashtags', 'cashtags', 'user_id', 'user_id_str',
       'username', 'name', 'day', 'hour', 'link', 'urls', 'photos', 'video',
       'thumbnail', 'retweet', 'nlikes', 'nreplies', 'nretweets', 'quote_url',
       'search', 'near', 'geo', 'source', 'user_rt_id', 'user_rt',
       'retweet_id', 'reply_to', 'retweet_date', 'translate', 'trans_src',
       'trans_dest'],
      dtype='object')
Index(['id', 'conversation_id', 'created_at', 'date', 'time', 'timezone',
       'user_id', 'username', 'name', 'place', 'tweet', 'language', 'mentions',
       'urls', 'photos', 'replies_count', 'retweets_count', 'nlikes',
       'hashtags', 'cashtags', 'link', 'retweet', 'quote_url', 'video',
       'thumbnail', 'near', 'geo', 'source', 'user_rt_id', 'user_rt',
       'retweet_id', 'reply_to', 'retweet_date', 'translate', 'trans_src',
       'trans_dest'],
      dtype='object')
Index(['id', 'conver

In [8]:
tweets_from_years['2021']

id      conversation_id  \
0     1476662222617251846  1476620230692679680   
1     1476656306610216960  1476644467578859528   
2     1476651519986614281  1476252898115964928   
3     1476619907076923398  1476252898115964928   
4     1476618021024190474  1476252898115964928   
...                   ...                  ...   
3110  1345384139969552389  1345382294966571008   
3111  1345382294966571008  1345382294966571008   
3112  1345344958710992897  1345334831719337984   
3113  1345208391958888448  1344675033231237120   
3114  1344810193952014336  1344518758707113986   

                                     created_at        date      time  \
0     2021-12-31 01:11:23 Arabian Standard Time  2021-12-31  01:11:23   
1     2021-12-31 00:47:53 Arabian Standard Time  2021-12-31  00:47:53   
2     2021-12-31 00:28:51 Arabian Standard Time  2021-12-31  00:28:51   
3     2021-12-30 22:23:14 Arabian Standard Time  2021-12-30  22:23:14   
4     2021-12-30 22:15:45 Arabian Standard Time  2021-12-30  22:15:45   
...                                         ...         ...       ...   
3110  2021-01-02 18:59:09 Arabian Standard Time  2021-01-02  18:59:09   
3111  2021-01-02 18:51:49 Arabian Standard Time  2021-01-02  18:51:49   
3112  2021-01-02 16:23:28 Arabian Standard Time  2021-01-02  16:23:28   
3113  2021-01-02 07:20:48 Arabian Standard Time  2021-01-02  07:20:48   
3114  2021-01-01 04:58:30 Arabian Standard Time  2021-01-01  04:58:30   

      timezone   user_id  username       name  place  ... geo source  \
0          400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
1          400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
2          400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
3          400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
4          400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
...        ...       ...       ...        ...    ...  ...  ..    ...   
3110       400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
3111       400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
3112       400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
3113       400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   
3114       400  44196397  elonmusk  Elon Musk    NaN  ... NaN    NaN   

     user_rt_id user_rt retweet_id  \
0           NaN     NaN        NaN   
1           NaN     NaN        NaN   
2           NaN     NaN        NaN   
3           NaN     NaN        NaN   
4           NaN     NaN        NaN   
...         ...     ...        ...   
3110        NaN     NaN        NaN   
3111        NaN     NaN        NaN   
3112        NaN     NaN        NaN   
3113        NaN     NaN        NaN   
3114        NaN     NaN        NaN   

                                               reply_to  retweet_date  \
0     [{'screen_name': 'roshanpateI', 'name': 'Rosha...           NaN   
1     [{'screen_name': 'tesla_raj', 'name': 'Tesla R...           NaN   
2     [{'screen_name': 'CSmithson80', 'name': 'Chris...           NaN   
3     [{'screen_name': 'BLKMDL3', 'name': 'Zack', 'i...           NaN   
4     [{'screen_name': 'mims', 'name': 'Christopher ...           NaN   
...                                                 ...           ...   
3110  [{'screen_name': 'flcnhvy', 'name': 'Viv ✶', '...           NaN   
3111                                                 []           NaN   
3112  [{'screen_name': 'newscientist', 'name': 'New ...           NaN   
3113  [{'screen_name': 'comma_ai', 'name': 'comma', ...           NaN   
3114  [{'screen_name': 'PPathole', 'name': 'Pranay P...           NaN   

      translate trans_src trans_dest  
0           NaN       NaN        NaN  
1           NaN       NaN        NaN  
2           NaN       NaN        NaN  
3           NaN       NaN        NaN  
4           NaN       NaN        NaN  
...         ...       ...        ...  
3110        NaN       NaN        NaN  
3111        NaN       NaN        N

In [9]:
for year in tweets_from_years:
    print(year)
    tweets_from_years[year] = tweets_from_years[year][['nlikes','date', 'link','photos','reply_to','retweet','source','tweet','video']]


2020
2021
2022
2019
2018
2015
2014
2016
2017
2013
2012
2010
2011


In [10]:
tweets_from_all_years = pd.concat([tweets_from_years[year] for year in tweets_from_years.keys()])
tweets_from_all_years = tweets_from_all_years.reset_index()

In [11]:
tweets_from_all_years = tweets_from_all_years[(tweets_from_all_years['reply_to']=='[]') & (tweets_from_all_years['retweet']==False)]

In [12]:
tweets_from_all_years

index  nlikes                 date  \
0          0   55085  2020-12-28 19:46:18   
3          3   33830  2020-12-28 17:23:31   
6          6  148037  2020-12-27 22:18:58   
34        34  187368  2020-12-25 20:54:29   
35        35  236833  2020-12-25 16:47:04   
...      ...     ...                  ...   
34873     22      53  2011-12-03 08:22:07   
34874     23      29  2011-12-03 08:20:28   
34875     24      78  2011-12-01 10:29:04   
34876     25     189  2011-12-01 09:55:11   
34877     26    4652  2010-06-04 18:31:57   

                                                    link  \
0      https://twitter.com/elonmusk/status/1343644462...   
3      https://twitter.com/elonmusk/status/1343608530...   
6      https://twitter.com/elonmusk/status/1343320495...   
34     https://twitter.com/elonmusk/status/1342574459...   
35     https://twitter.com/elonmusk/status/1342512194...   
...                                                  ...   
34873  https://twitter.com/elonmusk/status/1428812840...   
34874  https://twitter.com/elonmusk/status/1428808713...   
34875  https://twitter.com/elonmusk/status/1421884581...   
34876  https://twitter.com/elonmusk/status/1421799282...   
34877    https://twitter.com/elonmusk/status/15434727182   

                                                  photos reply_to  retweet  \
0                                                     []       []    False   
3                                                     []       []    False   
6                                                     []       []    False   
34                                                    []       []    False   
35     ['https://pbs.twimg.com/media/EqGPuYCUwAIb7_U....       []    False   
...                                                  ...      ...      ...   
34873                                                 []       []    False   
34874                                                 []       []    False   
34875                                                 []       []    False   
34876  ['https://pbs.twimg.com/media/Afkf5DMCAAEJGFr....       []    False   
34877                                                 []       []    False   

       source                                              tweet  video  
0         NaN  Entertainment will be critical when cars drive...      0  
3         NaN  What should Tesla do with in-car gaming in an ...      0  
6         NaN  Try playing Polytopia in your Tesla! Great gam...      0  
34        NaN  Change your horn sound to 🐐, 🐍🎷, 💨 or holiday ...      0  
35        NaN  Merry Christmas &amp; happy holidays! 🎁  https...      1  
...       ...                                                ...    ...  
34873     NaN                  That was a total non sequitur btw      0  
34874     NaN  Great Voltaire quote, arguably better than Twa...      0  
34875     NaN  I made the volume on the Model S  http://t.co/...      0  
34876     NaN  Went to Iceland on Sat to ride bumper cars on ...      1  
34877     NaN  Please ignore prior tweets, as that was someon...      0  

[16413 rows x 10 columns]

In [13]:
gen = pipeline('text-generation', model='gpt2')

2022-05-29 12:37:05.311881: I tensorflow/core/platform/cpu_feature_guard.cc:151] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [13]:


BOS_TOKEN = "<|elontext|>"
EOS_TOKEN = "<|endoftext|>"
PAD_TOKEN = "<|pad|>"
MAX_TOKENS = 512

tokenizer = AutoTokenizer.from_pretrained("gpt2",
    bos_token=BOS_TOKEN,
    eos_token=EOS_TOKEN,
    pad_token=PAD_TOKEN,
    max_length=MAX_TOKENS,
    is_split_into_words=True,
)

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


In [15]:
some_tweets = tweets_from_all_years.sample(n=10, random_state=30)
encoded = tokenizer(some_tweets['tweet'].to_list()[0], padding=True, max_length=MAX_TOKENS, pad_to_max_length=True,)
decoded = tokenizer.decode(encoded['input_ids'])
some_tokens=[]
for i in some_tweets['tweet']:
    some_tokens.append(' '.join(i.split(' ')[:5]))


/usr/local/lib/python3.9/site-packages/transformers/tokenization_utils_base.py:2301: UserWarning: `max_length` is ignored when `padding`=`True` and there is no truncation strategy. To pad to max length, use `padding='max_length'`.
  warnings.warn(
/usr/local/lib/python3.9/site-packages/transformers/tokenization_utils_base.py:2306: UserWarning: Though `pad_to_max_length` = `True`, it is ignored because `padding`=`True`.
  warnings.warn("Though `pad_to_max_length` = `True`, it is ignored because `padding`=`True`.")


In [16]:
some_tokens

['3 mins to liftoff',
 "Congratulations to @OrbitalSciences! “@CNETNews: Orbital's",
 'Noodles in Shinjuku  http://t.co/MWztTqByuA',
 'Starlink has been told by',
 'Drone spaceport ship heads to',
 'Excited about the Tesla Autopilot',
 'Rocket engines are healthy, but',
 'Preparing to launch a Thaicom',
 "Can't make this stuff up:",
 'First will rewatch Godfather Part']

In [17]:
for token in some_tokens:
    print(gen(token, max_length=50, num_return_sequences=1))

Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.
Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


[{'generated_text': '3 mins to liftoff\n\n11 mins to finish\n\n8 mins to exit\n\n17 mins to finish\n\n19 mins to finish\n\n16 mins to finished\n\nA total of 493kg were brought in. These included'}]


Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


[{'generated_text': "Congratulations to @OrbitalSciences! “@CNETNews: Orbital's JK Strahan reports on a demonstration of new robotic micro-pilots on the Space Coast\n\nOrbital Aerospace's JK Strahan"}]


Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


...

[{'generated_text': "Rocket engines are healthy, but there also needs to be other fuel sources. There's more information on this here: http://en.wikipedia.org/wiki/Jupiter_fire_engine"}]


Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


[{'generated_text': 'Preparing to launch a Thaicom LNG plant in Australia\'s biggest city will be particularly significant, as the next couple of years will be filled with work that will be more complex than one might expect.\n\n"We are going to be'}]


Setting `pad_token_id` to `eos_token_id`:50256 for open-end generation.


[{'generated_text': "Can't make this stuff up: I think that is why it is necessary. I don't think there are many problems beyond getting a good camera and decent frame rate! I think it's important that every aspect of a movie be handled better than what"}]
[{'generated_text': 'First will rewatch Godfather Part II: ReBoot, to get an idea of what happened next.\n\nAlso, in case anyone was wondering, how does the end of Godfather 2. The original plans for the film were scrapped as soon'}]


In [552]:
## Set tweets to subset or to full dataset
#tweet_ds = some_tweets
import datasets
tweet_ds = tweets_from_all_years
# Weil die Entwickler von Tensorflow nen schaden haben muss hier ein Datenset mit dem Datenset-Format der transformers library erstellt werden
tweets_ds = datasets.Dataset.from_pandas(tweet_ds[['tweet']])

tweets_ds = tweets_ds.train_test_split(test_size=0.2)
MAX_TOKENS = max([len(tokenizer.encode(tweet, add_special_tokens=True)) for tweet in tweet_ds['tweet']])+2

In [556]:
tweets_ds['train']

Dataset({
    features: ['tweet', '__index_level_0__'],
    num_rows: 13130
})

In [557]:
## taken from https://data-dive.com/finetune-german-gpt2-on-tpu-transformers-tensorflow-for-text-generation-of-reviews
def prepare_text(tweets:list):
    text = [BOS_TOKEN + tweet + EOS_TOKEN for tweet in tweets['tweet']]

    tokenized = tokenizer(
        text,
        add_special_tokens=True,  # Only adds pad not eos and bos
        max_length=MAX_TOKENS,
        truncation=True,
        pad_to_max_length=True,
    )
    tokenized["labels"] = tokenized["input_ids"].copy()
    #tokenized["labels"] = [x[1:] for x in tokenized["input_ids"]]
    #tokenized["labels"] = [
    #[-100 if x == tokenizer.pad_token_id else x for x in y]
    #for y in tokenized["labels"]
    #    ]
    # truncate input ids and attention mask to account for label shift
    #tokenized["input_ids"] = [x[:-1] for x in tokenized["input_ids"]]
    #tokenized["attention_mask"] = [x[:-1] for x in tokenized["attention_mask"]]

    return tokenized

In [558]:
tweets_ds = tweets_ds.map(
    prepare_text,
    batched=True,
    #num_proc=4,
    remove_columns=['tweet','__index_level_0__'],
    load_from_cache_file=True,
)

  0%|          | 0/14 [00:00<?, ?ba/s]

/usr/local/lib/python3.9/site-packages/transformers/tokenization_utils_base.py:2285: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(


  0%|          | 0/4 [00:00<?, ?ba/s]

In [560]:
tweets_ds['train']['input_ids']

[[50257,
  5703,
  4504,
  422,
  257,
  5296,
  284,
  3576,
  290,
  13643,
  11,
  810,
  314,
  1138,
  351,
  867,
  3499,
  661,
  13,
  314,
  1107,
  588,
  5491,
  0,
  50256,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258],
 [50257,
  3666,
  1561,
  379,
  38436,
  351,
  2488,
  36493,
  354,
  2442,
  220,
  220,
  2638,
  1378,
  83,
  13,
  1073,
  14,
  50,
  15285,
  85,
  89,
  54,
  67,
  49,
  1

In [561]:
for i in tweets_ds['train']:
    print(tokenizer.decode(i['input_ids']))

<|elontext|>Just returned from a trip to London and Oxford, where I met with many interesting people. I really like Britain!<|endoftext|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|>
<|elontext|>My talk at TED with @TEDchris   http://t.co/SNOvzWdR0u<|endoftext|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



<|elontext|>We didn’t even have kids back then. Just little sponges.<|endoftext|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|>
<|elontext|>There is no slowdown of the Gigafactory construction underway, as anyone near Reno with eyes can verify. It's not subtle.<|endoftext|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



<|elontext|> https://t.co/F23fxQkBCE<|endoftext|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|>
<|elontext|>Definitely going to need to rethink production planning...<|endoftext|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|><|pad|

In [562]:
tweets_ds['train']['input_ids']

[[50257,
  5703,
  4504,
  422,
  257,
  5296,
  284,
  3576,
  290,
  13643,
  11,
  810,
  314,
  1138,
  351,
  867,
  3499,
  661,
  13,
  314,
  1107,
  588,
  5491,
  0,
  50256,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258,
  50258],
 [50257,
  3666,
  1561,
  379,
  38436,
  351,
  2488,
  36493,
  354,
  2442,
  220,
  220,
  2638,
  1378,
  83,
  13,
  1073,
  14,
  50,
  15285,
  85,
  89,
  54,
  67,
  49,
  1

In [450]:
train_ds = prepare_text(tweets_train['tweet'])
test_ds = prepare_text(tweets_test['tweet'])

/usr/local/lib/python3.9/site-packages/transformers/tokenization_utils_base.py:2285: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  warnings.warn(


In [451]:

def build_tf_dataset(tokenized_texts, attention_mask, labels):
    # Create tf.data.Dataset

    #datasets.Dataset.from_pandas((tokenized_texts, attention_mask, labels))

    dataset = tf.data.Dataset.from_tensor_slices(
        ({
            'input_ids':tf.convert_to_tensor(tokenized_texts,name='input_ids'),
            'attention_mask':tf.convert_to_tensor(attention_mask, name='attention_mask'),
            'labels':tf.convert_to_tensor(labels, name='labels'),
    },
        tf.convert_to_tensor(labels, name='labels')
        )
    )
    return dataset

In [7]:
train =build_tf_dataset(train_ds['input_ids'], train_ds['attention_mask'], train_ds['labels'])
test =build_tf_dataset(test_ds['input_ids'], test_ds['attention_mask'],test_ds['labels'])

BUFFER_SIZE = len(train)
BATCH_SIZE = 32

NameError: name 'build_tf_dataset' is not defined

In [566]:


data_collator = DefaultDataCollator(return_tensors="tf")

In [567]:

train = tweets_ds['train'].to_tf_dataset(
    columns=["attention_mask", "input_ids", "labels"],
    shuffle=True,
    batch_size=16,
    collate_fn=data_collator,
)
test = tweets_ds['test'].to_tf_dataset(
    columns=["attention_mask", "input_ids", "labels"],
    shuffle=False,
    batch_size=16,
    collate_fn=data_collator,
)

In [568]:
train

<PrefetchDataset element_spec={'labels': TensorSpec(shape=(16, None), dtype=tf.int64, name=None), 'input_ids': TensorSpec(shape=(16, None), dtype=tf.int64, name=None), 'attention_mask': TensorSpec(shape=(16, None), dtype=tf.int64, name=None)}>

In [569]:

for i in train:
    print(i)
    print("sssssssss")
    #print(tokenizer.decode(i['input_ids']))
    #print(i[0]['input_ids'])

{'labels': <tf.Tensor: shape=(16, 95), dtype=int64, numpy=
array([[50257,  7222,   282, ..., 50258, 50258, 50258],
       [50257,  6425,    11, ..., 50258, 50258, 50258],
       [50257,    13,    31, ..., 50258, 50258, 50258],
       ...,
       [50257,  5703, 12047, ..., 50258, 50258, 50258],
       [50257, 11869, 16075, ..., 50258, 50258, 50258],
       [50257,  5840,   287, ..., 50258, 50258, 50258]])>, 'input_ids': <tf.Tensor: shape=(16, 95), dtype=int64, numpy=
array([[50257,  7222,   282, ..., 50258, 50258, 50258],
       [50257,  6425,    11, ..., 50258, 50258, 50258],
       [50257,    13,    31, ..., 50258, 50258, 50258],
       ...,
       [50257,  5703, 12047, ..., 50258, 50258, 50258],
       [50257, 11869, 16075, ..., 50258, 50258, 50258],
       [50257,  5840,   287, ..., 50258, 50258, 50258]])>, 'attention_mask': <tf.Tensor: shape=(16, 95), dtype=int64, numpy=
array([[1, 1, 1, ..., 0, 0, 0],
       [1, 1, 1, ..., 0, 0, 0],
       [1, 1, 1, ..., 0, 0, 0],
       ...,
    

In [570]:
train

<PrefetchDataset element_spec={'labels': TensorSpec(shape=(16, None), dtype=tf.int64, name=None), 'input_ids': TensorSpec(shape=(16, None), dtype=tf.int64, name=None), 'attention_mask': TensorSpec(shape=(16, None), dtype=tf.int64, name=None)}>

In [571]:
BUFFER_SIZE

12309

In [395]:
train = train.shuffle(len(train))#.batch(BATCH_SIZE)
test = test#.batch(BATCH_SIZE)

In [412]:
train

<BatchDataset element_spec=({'input_ids': TensorSpec(shape=(None, 94), dtype=tf.int32, name=None), 'attention_mask': TensorSpec(shape=(None, 94), dtype=tf.int32, name=None), 'labels': TensorSpec(shape=(None, 94), dtype=tf.int32, name=None)}, TensorSpec(shape=(None, 94), dtype=tf.int32, name=None))>

In [606]:

#model = AutoModelForCausalLM.from_pretrained("gpt2")
model = TFGPT2LMHeadModel.from_pretrained(
#model=TFAutoModelForCausalLM.from_pretrained(
    "gpt2",
    pad_token_id=tokenizer.pad_token_id,
    eos_token_id=tokenizer.eos_token_id,
    bos_token_id=tokenizer.bos_token_id,
)
model.resize_token_embeddings(len(tokenizer))
optimizer = AdamWeightDecay(lr=2e-5, weight_decay_rate=0.01)
model.compile(optimizer=optimizer)

All model checkpoint layers were used when initializing TFGPT2LMHeadModel.

All the layers of TFGPT2LMHeadModel were initialized from the model checkpoint at gpt2.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFGPT2LMHeadModel for predictions without further training.
/usr/local/lib/python3.9/site-packages/keras/optimizer_v2/adam.py:105: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super(Adam, self).__init__(name, **kwargs)
No loss specified in compile() - the model's internal loss computation will be used as the loss. Don't panic - this is a common way to train TensorFlow models in Transformers! To disable this behaviour, please pass a loss argument, or explicitly pass `loss=None` if you do not want your model to compute a loss.


In [607]:
model.fit(
    train,
    epochs=2,
    steps_per_epoch=BUFFER_SIZE / BATCH_SIZE,
)

Epoch 1/2
384/384 [==============================] - 16359s 43s/step - loss: 2.1567
Epoch 2/2
384/384 [==============================] - 24508s 64s/step - loss: 1.2140


In [610]:
model.save("./gpt2musktf")

INFO:tensorflow:Assets written to: ./gpt2musktf/assets


INFO:tensorflow:Assets written to: ./gpt2musktf/assets


## Hyperparameter Optimierung
Hyperparameter Optimierung hat bei generativen Sprachemodellen nur einen geringen Einfluss. Ein Modell ist aufgrund schlechterer Metriken, in der Wahrnehmung eines Menschen zwangsläufig schlechter. Im Voraus lässt sich dazu allerdings kein Beurteilung machen.

In [27]:
import keras_tuner as kt

In [ ]:
#tunable parameters
batch_size=16
lr=2e-5
num_train_epochs=5

In [ ]:
#https://wandb.ai/amogkam/transformers/reports/Hyperparameter-Optimization-for-Huggingface-Transformers--VmlldzoyMTc2ODI
class Model(kt.HyperModel):

    def build(self, hp: kt.HyperParameters):
        BATCH_SIZE = hp.Choice('batch_size',[4,8,16,32])
        model = TFGPT2LMHeadModel.from_pretrained(
            #model=TFAutoModelForCausalLM.from_pretrained(
            "gpt2",
            pad_token_id=tokenizer.pad_token_id,
            eos_token_id=tokenizer.eos_token_id,
            bos_token_id=tokenizer.bos_token_id,
        )
        model.resize_token_embeddings(len(tokenizer))
        optimizer = AdamWeightDecay(lr=hp.Choice('learning_rate', [2e-5, 3e-5, 5e-5]), weight_decay_rate=hp.Choice('weight_decay_rate',[0,0.01]))
        model.compile(optimizer=optimizer)
        return model
    def fit(self, hp, model, *args, **kwargs):
        return model.fit(
            train,
            batch_size= BATCH_SIZE,
            epochs=hp.Int('epochs',min_value=2, max_value=5),
            steps_per_epoch=BUFFER_SIZE / BATCH_SIZE,
        )


In [ ]:
tuner = kt.BayesianOptimization(
    objective="val_accuracy",
    max_trials=3,
    overwrite=True,
    directory="hyper-opt/",
    project_name="tune_musk",
)

In [604]:
tokenizer.decode([])

'!'

In [3]:
## Modell inference

In [9]:
model = TFGPT2LMHeadModel.from_pretrained("./gpt2musk")

All model checkpoint layers were used when initializing TFGPT2LMHeadModel.

All the layers of TFGPT2LMHeadModel were initialized from the model checkpoint at ./gpt2musk.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFGPT2LMHeadModel for predictions without further training.


In [12]:
gen = pipeline(
    "text-generation",
    model=model,
    tokenizer=tokenizer)

## Evaluate Models
Ein gene

In [21]:
#default model
gen(BOS_TOKEN)

[{'generated_text': '<|elontext|>The Falcon 9 rocket booster is the first real test of human capability against the most advanced  https://t.co/hUi8N1UbJg0'}]

In [ ]:
#default model mit tweet prompt

In [16]:
# trainiertes modell
gen(BOS_TOKEN)

[{'generated_text': "<|elontext|>- there's a lot of it  http://t.co/eBxXc1HdUj"}]

In [ ]:
#trainiertes modell mit tweet prompt

In [20]:
#trainiertes modell mit hyperparameter tuning
gen(BOS_TOKEN)

[{'generated_text': '<|elontext|>What I would like to do would be to publish the original version of this book on Wikipedia and then launch a-n-word petition campaign to  https://www.pixels.co/n6zzm1'}]

In [ ]:
#trainiertes distilgpt2 modell mit hyperparamerter tuning
gen(BOS_TOKEN)

In [ ]:
#trainiertes distilgpt2 modell mit hyperparamerter tuning mit tweet prompt

In [ ]:
# Loss berechnung aller gpt2 Modelle mit Tweet Prompt

In [ ]:
# Loss Berechnung aller distilgpt2 Modelle

In [35]:
TFGPT2LMHeadModel.from_pretrained('gpt2').compute_loss()

All model checkpoint layers were used when initializing TFGPT2LMHeadModel.

All the layers of TFGPT2LMHeadModel were initialized from the model checkpoint at gpt2.
If your task is similar to the task the model of the checkpoint was trained on, you can already use TFGPT2LMHeadModel for predictions without further training.


TypeError: 'NoneType' object is not callable

## Auswahl eines Modells für eine Evaluierung mit Testsubjekten
Mit einer Gruppe Studierender soll evaluiert werden ob es mit dem Modell möglich ist tweets zu generieren, die von echten Tweets nicht zu unterscheiden sind, dafür soll eines der Modelle ausgewählt werden.